In [ ]:
!unzip /content/Data4Datasphere.zip

Archive:  /content/Data4Datasphere.zip
  inflating: Organic_compounds_Morgan_FingerPrints.csv  
  inflating: Topology_features_organic_compounds.csv  
  inflating: Organic_compounds_coulomb_matrix_10x10.csv  


In [ ]:
from google.colab import files

In [ ]:
files.download('/content/Data4Datasphere.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Prepare Data

In [ ]:
import torch
import random
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split, KFold, cross_validate, cross_val_score
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

Using cuda device


In [ ]:
start_db = pd.read_csv('/content/drive/MyDrive/MSU_AI_Photocatal/Datasets/Organic_compound_final_dataset.csv')

In [ ]:
start_db

Unnamed: 0                                        Chromophore  \
0               0                             N#Cc1cc2ccc(O)cc2oc1=O   
1               1                          N#Cc1cc2ccc([O-])cc2oc1=O   
2               2  CCCCCCCCCCCC#CC#CCCCCCCCCCN1C(=O)c2ccc3c4ccc5c...   
3               3       [O-]c1c(-c2nc3ccccc3s2)cc2ccc3cccc4ccc1c2c34   
4               4       [O-]c1c(-c2nc3ccccc3s2)cc2ccc3cccc4ccc1c2c34   
...           ...                                                ...   
20231       20231    N#Cc1c(N2CCCC2)cc(-c2ccccc2)c2c1C(=O)c1ccccc1-2   
20232       20232   N#Cc1c(N2CCCCC2)cc(-c2ccccc2)c2c1C(=O)c1ccccc1-2   
20233       20233  N#Cc1c(N2CCCCC2)cc(-c2cccc3ccccc23)c2c1C(=O)c1...   
20234       20234  N#Cc1c(N2CCCCC2)cc(-c2ccc3ccccc3c2)c2c1C(=O)c1...   
20235       20235  N#Cc1c(N2CCCCC2)cc(-c2ccc3ccc4cccc5ccc2c3c45)c...   

         Solvent  Absorption max (nm)  Emission max (nm)  Lifetime (ns)  \
0              O                355.0         410.000000       2.804262   
1              O                408.0         450.000000       3.961965   
2      ClC(Cl)Cl                526.0         535.000000       3.602954   
3           CC#N                514.0         553.720000   29646.000000   
4        CS(C)=O                524.0         555.000000   45111.000000   
...          ...                  ...                ...            ...   
20231    C1CCOC1                358.0         500.243574   30238.556664   
20232    C1CCOC1                348.0         500.243574   30238.556664   
20233    C1CCOC1                344.0         460.000000   30238.556664   
20234    C1CCOC1                346.0         500.243574   30238.556664   
20235    C1CCOC1                344.0         473.000000   30238.556664   

       Quantum yield  Molecular weight (g mol-1)  
0           0.345025                   187.15370  
1           0.345025                   186.14576  
2           0.345025                  1061.54348  
3           0.345025                   350.42028  
4           0.345025                   350.42028  
...              ...                         ...  
20231       0.345025                   350.41992  
20232       0.345025                   364.44680  
20233       0.345025                   414.50668  
20234       0.345025                   414.50668  
20235       0.345025                   488.58856  

[20236 rows x 8 columns]

In [ ]:
change_nm = start_db['Absorption max (nm)']
change_nm_em = start_db['Emission max (nm)']
change_y = start_db['Quantum yield']

In [ ]:
morgan_full = pd.read_csv('/content/drive/MyDrive/MSU_AI_Photocatal/Datasets/Organic_compounds_descriptors/Organic_compounds_Morgan_FingerPrints.csv')
tda_full = pd.read_csv('/content/drive/MyDrive/MSU_AI_Photocatal/Datasets/Organic_compounds_descriptors/Topology_features_organic_compounds.csv')
CM_small = pd.read_csv('/content/drive/MyDrive/MSU_AI_Photocatal/Datasets/Organic_compounds_descriptors/Organic_compounds_coulomb_matrix_10x10.csv')

In [ ]:
CM_small_morgan_tda_db_y = pd.concat([CM_small, morgan_full, tda_full, pd.DataFrame({'Absorption':change_nm}),pd.DataFrame(start_db['Molecular weight (g mol-1)'])], axis=1).drop(['Unnamed: 0'],axis=1).drop_duplicates()

In [ ]:
CM_small_morgan_tda_db_y

CM_0       CM_1       CM_2       CM_3       CM_4       CM_5  \
0       73.516695  27.997891  13.467240  34.439686  34.058083  19.706623   
1       73.516695  27.976892  13.455964  34.530841  34.017921  12.919381   
2       73.516695   6.107871   5.398309  13.943743  24.061300   5.029020   
3      388.023441  30.379379  43.541950  55.501462  55.725541  34.437376   
4      388.023441  30.388456  43.540829  55.501775  55.726173  34.440258   
...           ...        ...        ...        ...        ...        ...   
20231   73.516695  10.267818  16.646469  39.624299  19.861808  13.674789   
20232   73.516695  10.325772  16.646947  39.627875  19.882118  13.664842   
20233   73.516695  10.593539  17.318980  39.597928  11.141309  19.911880   
20234   73.516695  10.327494  16.669343  39.627625  19.884228  13.664314   
20235   73.516695  10.325200  17.106724  39.621270  19.868371  13.619205   

            CM_6       CM_7       CM_8       CM_9  ...  solv_mean_H_1  \
0      11.124118  13.091766  19.696135  20.029354  ...       0.000000   
1      19.725661  11.123532  19.688135  19.965660  ...       0.000000   
2      39.173405   4.702785  13.554128   4.404038  ...       0.000000   
3      37.779617  24.568054  17.790142  18.827344  ...       0.000000   
4      37.779407  24.573775  17.791966  18.830626  ...       0.000000   
...          ...        ...        ...        ...  ...            ...   
20231  10.760305  15.596302  13.766413  10.062342  ...       0.815529   
20232  10.783155  15.647763  13.763316  10.051933  ...       0.815529   
20233  16.256344  13.408664   9.924419  20.379432  ...       0.815529   
20234  10.785643  15.652863  10.053468  13.757893  ...       0.815529   
20235  10.855447  15.777384  10.043878   5.810293  ...       0.815529   

       solv_mean_H_2  solv_std_H_0  solv_std_H_1  solv_std_H_2  \
0                0.0      0.000561           0.0           0.0   
1                0.0      0.000561           0.0           0.0   
2                0.0      0.293662           0.0           0.0   
3                0.0      0.139617           0.0           0.0   
4                0.0      0.301253           0.0           0.0   
...              ...           ...           ...           ...   
20231            0.0      0.143131           0.0           0.0   
20232            0.0      0.143131           0.0           0.0   
20233            0.0      0.143131           0.0           0.0   
20234            0.0      0.143131           0.0           0.0   
20235            0.0      0.143131           0.0           0.0   

       solv_entropy_H_0  solv_entropy_H_1  solv_entropy_H_2  Absorption  \
0              0.693147               0.0               0.0       355.0   
1              0.693147               0.0               0.0       408.0   
2              1.368031               0.0               0.0       526.0   
3              1.602776               0.0               0.0       514.0   
4              2.171758               0.0               0.0       524.0   
...                 ...               ...               ...         ...   
20231          2.072589              -0.0               0.0       358.0   
20232          2.072589              -0.0               0.0       348.0   
20233          2.072589              -0.0               0.0       344.0   
20234          2.072589              -0.0               0.0       346.0   
20235          2.072589              -0.0               0.0       344.0   

       Molecular weight (g mol-1)  
0                       187.15370  
1                       186.14576  
2                      1061.54348  
3                       350.42028  
4                       350.42028  
...                           ...  
20231                   350.41992  
20232                   364.44680  
20233                   414.50668  
20234                   414.50668  
20235                   488.58856  

[20205 rows x 4322 columns]

In [ ]:
import torch
from torch import nn

class NeuralNetwork(nn.Module):
    def __init__(self):
        super().__init__()
        self.layers_stack = nn.Sequential(
            nn.Linear(4321, 1024),
            nn.Dropout(0.2),
            nn.BatchNorm1d(1024),
            nn.ReLU(),
            nn.Linear(1024, 512),
            nn.Dropout(0.2),
            nn.BatchNorm1d(512),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Linear(128, 1),
        )

    def forward(self, x):
        logits = self.layers_stack(x)
        return logits

In [ ]:
import math
def log_cosh_loss(y_pred: torch.Tensor, y_true: torch.Tensor) -> torch.Tensor:
    def _log_cosh(x: torch.Tensor) -> torch.Tensor:
        return x + torch.nn.functional.softplus(-2. * x) - math.log(2.0)
    return torch.mean(_log_cosh(y_pred - y_true))

class LogCoshLoss(torch.nn.Module):
    def __init__(self):
        super().__init__()

    def forward(
        self, y_pred: torch.Tensor, y_true: torch.Tensor
    ) -> torch.Tensor:
        return log_cosh_loss(y_pred, y_true)

In [ ]:
x_train_solv, x_test_solv, y_train_solv, y_test_solv = train_test_split(np.array(CM_small_morgan_tda_db_y.loc[:, CM_small_morgan_tda_db_y.columns != 'Absorption'], dtype = np.float32), np.array(np.log(CM_small_morgan_tda_db_y['Absorption']), dtype = np.float32), test_size=0.2, random_state=42, shuffle=True)
x_val_solv, x_test_solv, y_val_solv, y_test_solv = train_test_split(x_test_solv, y_test_solv, test_size=0.2, random_state=42, shuffle=True)

In [ ]:
import torch

print("train_data.data:")
print("Type: ", type(x_train_solv.data))
print("Size: ", x_train_solv.shape)
print("Dtype:", x_train_solv.dtype)
print("Max:  ", np.max(x_train_solv.data))
print("Min:  ", np.min(x_train_solv.data))

train_data.data:
Type:  <class 'memoryview'>
Size:  (16164, 4321)
Dtype: float32
Max:   6874.357
Min:   -0.0


In [ ]:
mean = np.mean(x_train_solv.data)
std = np.std(x_train_solv.data)
print(f"mean = {mean:.2f}, std = {std:.2f}")

mean = 1.01, std = 21.83


In [ ]:
from torchvision import transforms

transform_with_normalize = transforms.Compose(
    [transforms.ToTensor(), transforms.Normalize(mean, std)]
)

print(transform_with_normalize)

Compose(
    ToTensor()
    Normalize(mean=1.0145918130874634, std=21.8330020904541)
)


In [ ]:
x_train = transform_with_normalize(x_train_solv)
x_val = transform_with_normalize(x_val_solv)

In [ ]:
x_test = transform_with_normalize(x_test_solv)

In [ ]:
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train.squeeze(), torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val.squeeze(), torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)

NameError: name 'x_train' is not defined

In [ ]:
import torch
import numpy as np
import random


def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)


set_random_seed(42)

In [ ]:
from sklearn.metrics import mean_absolute_error
def train_loop(dataloader, model, criterion, optimizer):
    num_batches = len(dataloader)

    train_loss = 0

    for imgs, labels in dataloader:
        # Compute prediction and loss
        pred = model(imgs.to(device)).squeeze(1)
        loss = criterion(pred, labels.to(device))

        # Optimization
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_loss += loss.item()

    train_loss /= num_batches
    print(f"Train loss: {train_loss:>8f}")

    return train_loss


def test_loop(dataloader, model, criterion, criterion_2):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    test_loss = 0
    test_loss_2 = 0

    with torch.no_grad():
        for imgs, labels in dataloader:
            # Compute prediction and loss
            pred = model(imgs.to(device)).squeeze(1)
            loss = criterion(pred, labels.to(device))
            #loss_2 = criterion_2(pred, labels.to(device))
            test_loss += loss.item()
            test_loss_2 += mean_absolute_error(pred.to('cpu').numpy(),labels.to('cpu').numpy())


    test_loss /= num_batches
    test_loss_2 /= num_batches
    print(f"Test loss: {test_loss:>8f}, test MRE: {test_loss_2} nm \n")

    return test_loss

In [ ]:
model = NeuralNetwork()
model.to(device)

NeuralNetwork(
  (layers_stack): Sequential(
    (0): Linear(in_features=4321, out_features=1024, bias=True)
    (1): Dropout(p=0.2, inplace=False)
    (2): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): ReLU()
    (4): Linear(in_features=1024, out_features=512, bias=True)
    (5): Dropout(p=0.2, inplace=False)
    (6): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (7): ReLU()
    (8): Linear(in_features=512, out_features=128, bias=True)
    (9): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): ReLU()
    (11): Linear(in_features=128, out_features=1, bias=True)
  )
)

In [ ]:
optimizer = torch.optim.Adam(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss() # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in range(num_epochs):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history["train"].append(train_loss)
    loss_history["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, '/content/drive/MyDrive/MSU_AI_Photocatal/Models/Organic_compounds_descriptors/MLP_absorption.pt')
            torch.save(model.state_dict(), '/content/drive/MyDrive/MSU_AI_Photocatal/Models/MLP_absorption_param.pth')
print("Done!")

Epoch 1
Train loss: 0.004565
Test loss: 0.005666, test MRE: 0.07794008929939832 nm 

Epoch 2
Train loss: 0.004608
Test loss: 0.005361, test MRE: 0.07806859691353406 nm 

Epoch 3
Train loss: 0.004363
Test loss: 0.006331, test MRE: 0.08619651958054188 nm 

Epoch 4
Train loss: 0.004374
Test loss: 0.005379, test MRE: 0.07813290827998928 nm 

Epoch 5
Train loss: 0.004840
Test loss: 0.005489, test MRE: 0.07950774083534877 nm 

Epoch 6
Train loss: 0.004277
Test loss: 0.005039, test MRE: 0.07559317102034886 nm 

Epoch 7
Train loss: 0.004398
Test loss: 0.005092, test MRE: 0.07596510341938804 nm 

Epoch 8
Train loss: 0.004246
Test loss: 0.005143, test MRE: 0.0745850217108633 nm 

Epoch 9
Train loss: 0.004356
Test loss: 0.004845, test MRE: 0.07409150182616477 nm 

Epoch 10
Train loss: 0.004464
Test loss: 0.005127, test MRE: 0.07536271199876186 nm 

Epoch 11
Train loss: 0.004314
Test loss: 0.005447, test MRE: 0.07910194744666417 nm 

Epoch 12
Train loss: 0.004105
Test loss: 0.005221, test MRE: 0.0

In [ ]:
if 100//100:
    print('Your')

Your


In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.squeeze().to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.026419123634696007
MAE : 10.730535507202148
RMSE : 22.109535217285156


# CNN

In [ ]:
x_train = transform_with_normalize(x_train_solv).permute(1,0,2)
x_val = transform_with_normalize(x_val_solv).permute(1,0,2)
x_test = transform_with_normalize(x_test_solv).permute(1,0,2)

In [ ]:
x_train.shape


torch.Size([16164, 1, 4321])

In [ ]:
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train, torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val, torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)

In [ ]:
import torch
from torch import nn
class CNN_small(nn.Module):
    def __init__(self):
        super().__init__()
        self.network = nn.Sequential(
            nn.Conv1d(1, 64, kernel_size=11,stride=4, padding=2),
            nn.Dropout(0.2),
            nn.BatchNorm1d(64),
            nn.ReLU(),
            nn.MaxPool1d(3, 2),
            nn.Conv1d(64, 192, kernel_size=5,stride=2),#, padding=2),
            nn.Dropout(0.2),
            nn.BatchNorm1d(192),
            nn.ReLU(),
            nn.MaxPool1d(3, 2),
            nn.Conv1d(192, 384, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(384),
            nn.ReLU(),
            nn.Conv1d(384, 256, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(256),
            nn.Conv1d(256, 128, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Conv1d(128, 128, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.MaxPool1d(3, 2),
            nn.AdaptiveAvgPool1d(6),
            nn.Flatten(),
            nn.Linear(768, 512),
            nn.Dropout(0.5),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.ReLU(),
            nn.Linear(128, 1))

    def forward(self, xb):
        return self.network(xb)

In [ ]:
model = CNN_small()
model.to(device)

CNN_small(
  (network): Sequential(
    (0): Conv1d(1, 64, kernel_size=(11,), stride=(4,), padding=(2,))
    (1): Dropout(p=0.2, inplace=False)
    (2): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): ReLU()
    (4): MaxPool1d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
    (5): Conv1d(64, 192, kernel_size=(5,), stride=(2,))
    (6): Dropout(p=0.2, inplace=False)
    (7): BatchNorm1d(192, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (8): ReLU()
    (9): MaxPool1d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
    (10): Conv1d(192, 384, kernel_size=(3,), stride=(1,), padding=(1,))
    (11): Dropout(p=0.2, inplace=False)
    (12): BatchNorm1d(384, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (13): ReLU()
    (14): Conv1d(384, 256, kernel_size=(3,), stride=(1,), padding=(1,))
    (15): Dropout(p=0.2, inplace=False)
    (16): BatchNorm1d(256, eps=1e-05, momentum=0.1

In [ ]:
from tqdm import tqdm
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_cnn = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_cnn["train"].append(train_loss)
    loss_history_cnn["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//CNN_absorption.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models//CNN_absorption_param.pth')
print("Done!")

Train loss: 0.001175


 85%|████████▍ | 16912/20000 [17:08:08<3:08:50,  3.67s/it]

Test loss: 0.002539, test MRE: 0.047690825135100125 nm 

Epoch 16913
Train loss: 0.001190


 85%|████████▍ | 16913/20000 [17:08:11<3:09:10,  3.68s/it]

Test loss: 0.002571, test MRE: 0.04769435554158454 nm 

Epoch 16914
Train loss: 0.001154


...

Test loss: 0.002629, test MRE: 0.04801513517604155 nm 

Epoch 16921
Train loss: 0.001167


 85%|████████▍ | 16921/20000 [17:08:40<3:06:30,  3.63s/it]

Test loss: 0.002637, test MRE: 0.04762561590063805 nm 

Epoch 16922


 85%|████████▍ | 16921/20000 [17:08:43<3:07:11,  3.65s/it]


KeyboardInterrupt: 

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.04799489304423332
MAE : 20.167423248291016
RMSE : 33.10823440551758


# RNN

In [ ]:
from torch import nn
class AbsorptionRNN(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim, num_layers):
        super(AbsorptionRNN, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_layers = num_layers

        self.rnn = nn.RNN(input_dim, hidden_dim, num_layers, batch_first=True, dropout=0.2)
        self.fc = nn.Linear(hidden_dim, output_dim)

    def forward(self, x):
        h0 = torch.zeros(self.num_layers, x.size(0), self.hidden_dim).to(x.device)
        out, _ = self.rnn(x, h0)
        out = self.fc(out[:, -1, :])
        return out
model = AbsorptionRNN(input_dim=4321, hidden_dim=128, num_layers=2, output_dim=1)
model.to(device)

In [ ]:
model = AbsorptionRNN(input_dim=4321, hidden_dim=128, num_layers=2, output_dim=1)
model.to(device)

AbsorptionRNN(
  (rnn): RNN(4321, 128, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=128, out_features=1, bias=True)
)

In [ ]:
import pickle
from tqdm import tqdm
optimizer = torch.optim.AdamW(model.parameters(), lr=5e-5)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_rnn = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_rnn["train"].append(train_loss)
    loss_history_rnn["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//RNN_absorption.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models//RNN_absorption_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.05027267709374428
MAE : 20.918886184692383
RMSE : 31.025924682617188


# GRU

In [ ]:
import torch.nn as nn
import torch

class BiDirectionalGRU(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, dropout):
        super(BiDirectionalGRU, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.dropout = nn.Dropout(dropout)

        self.gru = nn.GRU(input_size=input_size,
                         hidden_size=hidden_size,
                         num_layers=num_layers,
                         batch_first=True,
                          dropout = 0.2)

        self.fc = nn.Linear(hidden_size, 1)  # 2 for bidirectional

    def forward(self, x):
        # x shape: (batch_size, seq_len, input_size)
        out, _ = self.gru(x)
        out = self.dropout(out)

        # Take the final hidden state of the bidirectional GRU
        out = out[:, -1, :]  # (batch_size, hidden_size * 2)

        out = self.fc(out)
        return out

In [ ]:
model = BiDirectionalGRU(4321, 128, 2, 0.2)
model.to(device)

BiDirectionalGRU(
  (dropout): Dropout(p=0.2, inplace=False)
  (gru): GRU(4321, 128, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=128, out_features=1, bias=True)
)

In [ ]:
import pickle
from tqdm import tqdm
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_gru = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_gru["train"].append(train_loss)
    loss_history_gru["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//GRU_absorption.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models//GRU_absorption_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.05438702553510666
MAE : 22.637176513671875
RMSE : 35.81822967529297


# EM

In [ ]:
CM_small_morgan_tda_db_em = pd.concat([CM_small, morgan_full, tda_full, pd.DataFrame({'Emission':change_nm_em}),pd.DataFrame(start_db['Molecular weight (g mol-1)'])], axis=1).drop(['Unnamed: 0'],axis=1).drop_duplicates()

In [ ]:
x_train_solv, x_test_solv, y_train_solv, y_test_solv = train_test_split(np.array(CM_small_morgan_tda_db_em.loc[:, CM_small_morgan_tda_db_em.columns != 'Emission'], dtype = np.float32), np.array(np.log(CM_small_morgan_tda_db_em['Emission']), dtype = np.float32), test_size=0.2, random_state=42, shuffle=True)
x_val_solv, x_test_solv, y_val_solv, y_test_solv = train_test_split(x_test_solv, y_test_solv, test_size=0.2, random_state=42, shuffle=True)

In [ ]:
mean = np.mean(x_train_solv.data)
std = np.std(x_train_solv.data)
print(f"mean = {mean:.2f}, std = {std:.2f}")

mean = 1.01, std = 21.78


In [ ]:
from torchvision import transforms

transform_with_normalize = transforms.Compose(
    [transforms.ToTensor(), transforms.Normalize(mean, std)]
)

print(transform_with_normalize)
x_train = transform_with_normalize(x_train_solv)
x_val = transform_with_normalize(x_val_solv)
x_test = transform_with_normalize(x_test_solv)
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train.squeeze(), torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val.squeeze(), torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)

Compose(
    ToTensor()
    Normalize(mean=1.0148704051971436, std=21.77751350402832)
)


# FCN_EM

In [ ]:
import torch
from torch import nn

class NeuralNetwork(nn.Module):
    def __init__(self):
        super().__init__()
        self.layers_stack = nn.Sequential(
            nn.Linear(4321, 1024),
            nn.Dropout(0.2),
            nn.BatchNorm1d(1024),
            nn.ReLU(),
            nn.Linear(1024, 512),
            nn.Dropout(0.2),
            nn.BatchNorm1d(512),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Linear(128, 1),
        )

    def forward(self, x):
        logits = self.layers_stack(x)
        return logits
import math
def log_cosh_loss(y_pred: torch.Tensor, y_true: torch.Tensor) -> torch.Tensor:
    def _log_cosh(x: torch.Tensor) -> torch.Tensor:
        return x + torch.nn.functional.softplus(-2. * x) - math.log(2.0)
    return torch.mean(_log_cosh(y_pred - y_true))



In [ ]:
class LogCoshLoss(torch.nn.Module):
    def __init__(self):
        super().__init__()

    def forward(
        self, y_pred: torch.Tensor, y_true: torch.Tensor
    ) -> torch.Tensor:
        return log_cosh_loss(y_pred, y_true)
import torch
import numpy as np
import random


def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)


set_random_seed(42)

In [ ]:
import torch
import numpy as np
import random


def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)


set_random_seed(42)

In [ ]:
from sklearn.metrics import mean_absolute_error
def train_loop(dataloader, model, criterion, optimizer):
    num_batches = len(dataloader)

    train_loss = 0

    for imgs, labels in dataloader:
        # Compute prediction and loss
        pred = model(imgs.to(device)).squeeze(1)
        loss = criterion(pred, labels.to(device))

        # Optimization
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_loss += loss.item()

    train_loss /= num_batches
    print(f"Train loss: {train_loss:>8f}")

    return train_loss


def test_loop(dataloader, model, criterion, criterion_2):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    test_loss = 0
    test_loss_2 = 0

    with torch.no_grad():
        for imgs, labels in dataloader:
            # Compute prediction and loss
            pred = model(imgs.to(device)).squeeze(1)
            loss = criterion(pred, labels.to(device))
            #loss_2 = criterion_2(pred, labels.to(device))
            test_loss += loss.item()
            test_loss_2 += mean_absolute_error(pred.to('cpu').numpy(),labels.to('cpu').numpy())


    test_loss /= num_batches
    test_loss_2 /= num_batches
    print(f"Test loss: {test_loss:>8f}, test MRE: {test_loss_2} nm \n")

    return test_loss

In [ ]:
model = NeuralNetwork()
model.to(device)

NeuralNetwork(
  (layers_stack): Sequential(
    (0): Linear(in_features=4321, out_features=1024, bias=True)
    (1): Dropout(p=0.2, inplace=False)
    (2): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): ReLU()
    (4): Linear(in_features=1024, out_features=512, bias=True)
    (5): Dropout(p=0.2, inplace=False)
    (6): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (7): ReLU()
    (8): Linear(in_features=512, out_features=128, bias=True)
    (9): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): ReLU()
    (11): Linear(in_features=128, out_features=1, bias=True)
  )
)

In [ ]:
from tqdm import tqdm
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_em = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_em["train"].append(train_loss)
    loss_history_em["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//FCN_emission.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models//FCN_emission_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.squeeze().to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.041310686618089676
MAE : 20.387529373168945
RMSE : 31.7388973236084


# CNN_EM

In [ ]:
x_train = transform_with_normalize(x_train_solv).permute(1,0,2)
x_val = transform_with_normalize(x_val_solv).permute(1,0,2)

In [ ]:
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train, torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val, torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)


In [ ]:
import torch
from torch import nn
class CNN_small(nn.Module):
    def __init__(self):
        super().__init__()
        self.network = nn.Sequential(
            nn.Conv1d(1, 64, kernel_size=11,stride=4, padding=2),
            nn.Dropout(0.2),
            nn.BatchNorm1d(64),
            nn.ReLU(),
            nn.MaxPool1d(3, 2),
            nn.Conv1d(64, 192, kernel_size=5,stride=2),#, padding=2),
            nn.Dropout(0.2),
            nn.BatchNorm1d(192),
            nn.ReLU(),
            nn.MaxPool1d(3, 2),
            nn.Conv1d(192, 384, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(384),
            nn.ReLU(),
            nn.Conv1d(384, 256, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(256),
            nn.Conv1d(256, 128, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Conv1d(128, 128, kernel_size=3,padding=1),
            nn.Dropout(0.2),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.MaxPool1d(3, 2),
            nn.AdaptiveAvgPool1d(6),
            nn.Flatten(),
            nn.Linear(768, 512),
            nn.Dropout(0.5),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.ReLU(),
            nn.Linear(128, 1))

    def forward(self, xb):
        return self.network(xb)

In [ ]:
import math
def log_cosh_loss(y_pred: torch.Tensor, y_true: torch.Tensor) -> torch.Tensor:
    def _log_cosh(x: torch.Tensor) -> torch.Tensor:
        return x + torch.nn.functional.softplus(-2. * x) - math.log(2.0)
    return torch.mean(_log_cosh(y_pred - y_true))
class LogCoshLoss(torch.nn.Module):
    def __init__(self):
        super().__init__()

    def forward(
        self, y_pred: torch.Tensor, y_true: torch.Tensor
    ) -> torch.Tensor:
        return log_cosh_loss(y_pred, y_true)

In [ ]:
from sklearn.metrics import mean_absolute_error
def train_loop(dataloader, model, criterion, optimizer):
    num_batches = len(dataloader)

    train_loss = 0

    for imgs, labels in dataloader:
        # Compute prediction and loss
        pred = model(imgs.to(device)).squeeze(1)
        loss = criterion(pred, labels.to(device))

        # Optimization
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_loss += loss.item()

    train_loss /= num_batches
    print(f"Train loss: {train_loss:>8f}")

    return train_loss


def test_loop(dataloader, model, criterion, criterion_2):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    test_loss = 0
    test_loss_2 = 0

    with torch.no_grad():
        for imgs, labels in dataloader:
            # Compute prediction and loss
            pred = model(imgs.to(device)).squeeze(1)
            loss = criterion(pred, labels.to(device))
            #loss_2 = criterion_2(pred, labels.to(device))
            test_loss += loss.item()
            test_loss_2 += mean_absolute_error(pred.to('cpu').numpy(),labels.to('cpu').numpy())


    test_loss /= num_batches
    test_loss_2 /= num_batches
    print(f"Test loss: {test_loss:>8f}, test MRE: {test_loss_2} nm \n")

    return test_loss

In [ ]:
model = CNN_small()
model.to(device)

CNN_small(
  (network): Sequential(
    (0): Conv1d(1, 64, kernel_size=(11,), stride=(4,), padding=(2,))
    (1): Dropout(p=0.2, inplace=False)
    (2): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): ReLU()
    (4): MaxPool1d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
    (5): Conv1d(64, 192, kernel_size=(5,), stride=(2,))
    (6): Dropout(p=0.2, inplace=False)
    (7): BatchNorm1d(192, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (8): ReLU()
    (9): MaxPool1d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
    (10): Conv1d(192, 384, kernel_size=(3,), stride=(1,), padding=(1,))
    (11): Dropout(p=0.2, inplace=False)
    (12): BatchNorm1d(384, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (13): ReLU()
    (14): Conv1d(384, 256, kernel_size=(3,), stride=(1,), padding=(1,))
    (15): Dropout(p=0.2, inplace=False)
    (16): BatchNorm1d(256, eps=1e-05, momentum=0.1

In [ ]:
from tqdm import tqdm
import pickle
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_cnn_em = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_cnn_em["train"].append(train_loss)
    loss_history_cnn_em["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, '/content/drive/MyDrive/MSU_AI_Photocatal/Models//CNN_em.pt')
            torch.save(model.state_dict(), '/content/drive/MyDrive/MSU_AI_Photocatal/Models//CNN_em_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

# RNN_EM

In [ ]:
x_train = transform_with_normalize(x_train_solv).permute(1,0,2)
x_val = transform_with_normalize(x_val_solv).permute(1,0,2)
x_test = transform_with_normalize(x_test_solv).permute(1,0,2)


In [ ]:
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train, torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val, torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)


In [ ]:
from torch import nn
class EmRNN(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim, num_layers):
        super(EmRNN, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_layers = num_layers

        self.rnn = nn.RNN(input_dim, hidden_dim, num_layers, batch_first=True, dropout=0.2)
        self.fc = nn.Linear(hidden_dim, output_dim)

    def forward(self, x):
        h0 = torch.zeros(self.num_layers, x.size(0), self.hidden_dim).to(x.device)
        out, _ = self.rnn(x, h0)
        out = self.fc(out[:, -1, :])
        return out


In [ ]:
model = EmRNN(input_dim=4321, hidden_dim=128, num_layers=2, output_dim=1)
model.to(device)

EmRNN(
  (rnn): RNN(4321, 128, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=128, out_features=1, bias=True)
)

In [ ]:
import math
def log_cosh_loss(y_pred: torch.Tensor, y_true: torch.Tensor) -> torch.Tensor:
    def _log_cosh(x: torch.Tensor) -> torch.Tensor:
        return x + torch.nn.functional.softplus(-2. * x) - math.log(2.0)
    return torch.mean(_log_cosh(y_pred - y_true))
class LogCoshLoss(torch.nn.Module):
    def __init__(self):
        super().__init__()

    def forward(
        self, y_pred: torch.Tensor, y_true: torch.Tensor
    ) -> torch.Tensor:
        return log_cosh_loss(y_pred, y_true)
import torch
import numpy as np
import random


def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)


set_random_seed(42)

In [ ]:
from sklearn.metrics import mean_absolute_error
def train_loop(dataloader, model, criterion, optimizer):
    num_batches = len(dataloader)

    train_loss = 0

    for imgs, labels in dataloader:
        # Compute prediction and loss
        pred = model(imgs.to(device)).squeeze(1)
        loss = criterion(pred, labels.to(device))

        # Optimization
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_loss += loss.item()

    train_loss /= num_batches
    print(f"Train loss: {train_loss:>8f}")

    return train_loss


def test_loop(dataloader, model, criterion, criterion_2):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    test_loss = 0
    test_loss_2 = 0

    with torch.no_grad():
        for imgs, labels in dataloader:
            # Compute prediction and loss
            pred = model(imgs.to(device)).squeeze(1)
            loss = criterion(pred, labels.to(device))
            #loss_2 = criterion_2(pred, labels.to(device))
            test_loss += loss.item()
            test_loss_2 += mean_absolute_error(pred.to('cpu').numpy(),labels.to('cpu').numpy())


    test_loss /= num_batches
    test_loss_2 /= num_batches
    print(f"Test loss: {test_loss:>8f}, test MRE: {test_loss_2} nm \n")

    return test_loss

In [ ]:
from tqdm import tqdm
optimizer = torch.optim.Adam(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss() # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_em_rnn = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in range(num_epochs):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_em_rnn["train"].append(train_loss)
    loss_history_em_rnn["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, '/content/drive/MyDrive/MSU_AI_Photocatal/Models//RNN_emission.pt')
            torch.save(model.state_dict(), '/content/drive/MyDrive/MSU_AI_Photocatal/Models//RNN_emission_param.pth')
print("Done!")

Epoch 1
Train loss: 0.402002
Test loss: 0.023675, test MRE: 0.16829398595819287 nm 

Epoch 2
Train loss: 0.020078
Test loss: 0.017894, test MRE: 0.15117777650262795 nm 

Epoch 3
Train loss: 0.016905
Test loss: 0.016246, test MRE: 0.14612959003915973 nm 

Epoch 4
Train loss: 0.015698
Test loss: 0.015250, test MRE: 0.14211809372200684 nm 

Epoch 5
Train loss: 0.014748
Test loss: 0.014808, test MRE: 0.14075549428953843 nm 

Epoch 6
Train loss: 0.014111
Test loss: 0.014424, test MRE: 0.13903873340756284 nm 

Epoch 7
Train loss: 0.013780
Test loss: 0.013597, test MRE: 0.13372062628760056 nm 

Epoch 8
Train loss: 0.013345
Test loss: 0.013504, test MRE: 0.13213843165659436 nm 

Epoch 9
Train loss: 0.012889
Test loss: 0.013096, test MRE: 0.13052673170379564 nm 

Epoch 10
Train loss: 0.012586
Test loss: 0.012586, test MRE: 0.12800205265190087 nm 

Epoch 11
Train loss: 0.012199
Test loss: 0.012366, test MRE: 0.1255572920336443 nm 

Epoch 12
Train loss: 0.011869
Test loss: 0.012349, test MRE: 0.1

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.05132341757416725
MAE : 25.00152015686035
RMSE : 35.82727813720703


# GRU_EM

In [ ]:
import torch.nn as nn
import torch

class BiDirectionalGRU(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, dropout):
        super(BiDirectionalGRU, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.dropout = nn.Dropout(dropout)

        self.gru = nn.GRU(input_size=input_size,
                         hidden_size=hidden_size,
                         num_layers=num_layers,
                         batch_first=True,
                          dropout = 0.2)

        self.fc = nn.Linear(hidden_size, 1)  # 2 for bidirectional

    def forward(self, x):
        # x shape: (batch_size, seq_len, input_size)
        out, _ = self.gru(x)
        out = self.dropout(out)

        # Take the final hidden state of the bidirectional GRU
        out = out[:, -1, :]  # (batch_size, hidden_size * 2)

        out = self.fc(out)
        return out

In [ ]:
model = BiDirectionalGRU(4321, 128, 2, 0.2)
model.to(device)

BiDirectionalGRU(
  (dropout): Dropout(p=0.2, inplace=False)
  (gru): GRU(4321, 128, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=128, out_features=1, bias=True)
)

In [ ]:
import pickle
from tqdm import tqdm
model = BiDirectionalGRU(4321, 128, 2, 0.2)
model.to(device)
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_gru_em = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_gru_em["train"].append(train_loss)
    loss_history_gru_em["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//GRU_em.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models/GRU_em_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.05431298911571503
MAE : 26.719276428222656
RMSE : 37.375919342041016


# EM + Absorption

In [ ]:
CM_small_morgan_tda_db_em = pd.concat([CM_small, morgan_full, tda_full, pd.DataFrame({'Emission':change_nm_em}),pd.DataFrame(start_db['Molecular weight (g mol-1)'])], axis=1).drop(['Unnamed: 0'],axis=1).drop_duplicates()

In [ ]:
x_train_solv, x_test_solv, y_train_solv, y_test_solv = train_test_split(np.array(CM_small_morgan_tda_db_em.loc[:, CM_small_morgan_tda_db_em.columns != 'Emission'], dtype = np.float32), np.array(np.log(CM_small_morgan_tda_db_em['Emission']), dtype = np.float32), test_size=0.2, random_state=42, shuffle=True)
x_val_solv, x_test_solv, y_val_solv, y_test_solv = train_test_split(x_test_solv, y_test_solv, test_size=0.2, random_state=42, shuffle=True)

In [ ]:
mean = np.mean(x_train_solv.data)
std = np.std(x_train_solv.data)
print(f"mean = {mean:.2f}, std = {std:.2f}")

mean = 1.01, std = 21.78


In [ ]:
from torchvision import transforms

transform_with_normalize = transforms.Compose(
    [transforms.ToTensor(), transforms.Normalize(mean, std)]
)

print(transform_with_normalize)
x_train = transform_with_normalize(x_train_solv)
x_val = transform_with_normalize(x_val_solv)
x_test = transform_with_normalize(x_test_solv)

Compose(
    ToTensor()
    Normalize(mean=1.0148704051971436, std=21.77751350402832)
)


In [ ]:
import torch
from torch import nn

class NeuralNetwork(nn.Module):
    def __init__(self):
        super().__init__()
        self.layers_stack = nn.Sequential(
            nn.Linear(4321, 1024),
            nn.Dropout(0.2),
            nn.BatchNorm1d(1024),
            nn.ReLU(),
            nn.Linear(1024, 512),
            nn.Dropout(0.2),
            nn.BatchNorm1d(512),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Linear(128, 1),
        )

    def forward(self, x):
        logits = self.layers_stack(x)
        return logits

In [ ]:
model_abs = torch.load('content/drive/MyDrive/MSU_AI_Photocatal/Models//MLP_absorption.pt', weights_only=False)
model_abs.eval()
model_abs.to(device)

NeuralNetwork(
  (layers_stack): Sequential(
    (0): Linear(in_features=4321, out_features=1024, bias=True)
    (1): Dropout(p=0.2, inplace=False)
    (2): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): ReLU()
    (4): Linear(in_features=1024, out_features=512, bias=True)
    (5): Dropout(p=0.2, inplace=False)
    (6): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (7): ReLU()
    (8): Linear(in_features=512, out_features=128, bias=True)
    (9): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): ReLU()
    (11): Linear(in_features=128, out_features=1, bias=True)
  )
)

In [ ]:
device

'cuda'

In [ ]:
abs_train = model_abs(x_train.squeeze().to(device)).squeeze(1)
abs_val = model_abs(x_val.squeeze().to(device)).squeeze(1)
abs_test = model_abs(x_test.squeeze().to(device)).squeeze(1)
abs_train.shape

torch.Size([16168])

In [ ]:
abs_train = np.exp(np.expand_dims(abs_train.detach().to('cpu').numpy(), axis=1))
abs_val = np.exp(np.expand_dims(abs_val.detach().to('cpu').numpy(), axis=1))
abs_test = np.exp(np.expand_dims(abs_test.detach().to('cpu').numpy(), axis=1))

In [ ]:
x_train_solv = np.concatenate((x_train_solv, abs_train),axis=1)
x_val_solv = np.concatenate((x_val_solv, abs_val),axis=1)
x_test_solv = np.concatenate((x_test_solv, abs_test),axis=1)

# After prepared data

In [ ]:
mean = np.mean(x_train_solv.data)
std = np.std(x_train_solv.data)
print(f"mean = {mean:.2f}, std = {std:.2f}")

mean = 1.01, std = 21.83


In [ ]:
from torchvision import transforms

transform_with_normalize = transforms.Compose(
    [transforms.ToTensor(), transforms.Normalize(mean, std)]
)

print(transform_with_normalize)
x_train = transform_with_normalize(x_train_solv)
x_val = transform_with_normalize(x_val_solv)
x_test = transform_with_normalize(x_test_solv)

Compose(
    ToTensor()
    Normalize(mean=1.0145918130874634, std=21.8330020904541)
)


In [ ]:
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train.squeeze(), torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val.squeeze(), torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)

In [ ]:
import torch
from torch import nn

class NeuralNetwork_EM_ABS(nn.Module):
    def __init__(self):
        super().__init__()
        self.layers_stack = nn.Sequential(
            nn.Linear(4322, 1024),
            nn.Dropout(0.2),
            nn.BatchNorm1d(1024),
            nn.ReLU(),
            nn.Linear(1024, 512),
            nn.Dropout(0.2),
            nn.BatchNorm1d(512),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Linear(128, 1),
        )

    def forward(self, x):
        logits = self.layers_stack(x)
        return logits



In [ ]:
import math
def log_cosh_loss(y_pred: torch.Tensor, y_true: torch.Tensor) -> torch.Tensor:
    def _log_cosh(x: torch.Tensor) -> torch.Tensor:
        return x + torch.nn.functional.softplus(-2. * x) - math.log(2.0)
    return torch.mean(_log_cosh(y_pred - y_true))
class LogCoshLoss(torch.nn.Module):
    def __init__(self):
        super().__init__()

    def forward(
        self, y_pred: torch.Tensor, y_true: torch.Tensor
    ) -> torch.Tensor:
        return log_cosh_loss(y_pred, y_true)
import torch
import numpy as np
import random


def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)


set_random_seed(42)

In [ ]:
model = NeuralNetwork_EM_ABS()
model.to(device)

NeuralNetwork_EM_ABS(
  (layers_stack): Sequential(
    (0): Linear(in_features=4322, out_features=1024, bias=True)
    (1): Dropout(p=0.2, inplace=False)
    (2): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): ReLU()
    (4): Linear(in_features=1024, out_features=512, bias=True)
    (5): Dropout(p=0.2, inplace=False)
    (6): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (7): ReLU()
    (8): Linear(in_features=512, out_features=128, bias=True)
    (9): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): ReLU()
    (11): Linear(in_features=128, out_features=1, bias=True)
  )
)

In [ ]:
from sklearn.metrics import mean_absolute_error
def train_loop(dataloader, model, criterion, optimizer):
    num_batches = len(dataloader)

    train_loss = 0

    for imgs, labels in dataloader:
        # Compute prediction and loss
        pred = model(imgs.to(device)).squeeze(1)
        loss = criterion(pred, labels.to(device))

        # Optimization
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_loss += loss.item()

    train_loss /= num_batches
    print(f"Train loss: {train_loss:>8f}")

    return train_loss


def test_loop(dataloader, model, criterion, criterion_2):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    test_loss = 0
    test_loss_2 = 0

    with torch.no_grad():
        for imgs, labels in dataloader:
            # Compute prediction and loss
            pred = model(imgs.to(device)).squeeze(1)
            loss = criterion(pred, labels.to(device))
            #loss_2 = criterion_2(pred, labels.to(device))
            test_loss += loss.item()
            test_loss_2 += mean_absolute_error(pred.to('cpu').numpy(),labels.to('cpu').numpy())


    test_loss /= num_batches
    test_loss_2 /= num_batches
    print(f"Test loss: {test_loss:>8f}, test MRE: {test_loss_2} nm \n")

    return test_loss


In [ ]:
from tqdm import tqdm
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_abs_em = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_abs_em["train"].append(train_loss)
    loss_history_abs_em["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models/FCN_abs_emission.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models/FCN_abs_emission_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.squeeze().to(device)).squeeze(1).detach().to('cpu').numpy()#
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.03963368013501167
MAE : 19.60666847229004
RMSE : 31.64255714416504


# RNN_abs_em

In [ ]:
x_train = transform_with_normalize(x_train_solv).permute(1,0,2)
x_val = transform_with_normalize(x_val_solv).permute(1,0,2)
x_test = transform_with_normalize(x_test_solv).permute(1,0,2)



In [ ]:
from torch.utils.data import DataLoader
import torch.utils.data as data_utils
batch_size = 64
dataset_train = data_utils.TensorDataset(x_train, torch.from_numpy(y_train_solv))
dataset_val = data_utils.TensorDataset(x_val, torch.from_numpy(y_val_solv))
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, num_workers=2)
val_loader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, num_workers=2)

In [ ]:
from torch import nn
class Em_abs_RNN(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim, num_layers):
        super(Em_abs_RNN, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_layers = num_layers

        self.rnn = nn.RNN(input_dim, hidden_dim, num_layers, batch_first=True, dropout=0.2)
        self.fc = nn.Linear(hidden_dim, output_dim)

    def forward(self, x):
        h0 = torch.zeros(self.num_layers, x.size(0), self.hidden_dim).to(x.device)
        out, _ = self.rnn(x, h0)
        out = self.fc(out[:, -1, :])
        return out


In [ ]:
model = Em_abs_RNN(input_dim=4322, hidden_dim=128, num_layers=2, output_dim=1)
model.to(device)


Em_abs_RNN(
  (rnn): RNN(4322, 128, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=128, out_features=1, bias=True)
)

In [ ]:
import math
def log_cosh_loss(y_pred: torch.Tensor, y_true: torch.Tensor) -> torch.Tensor:
    def _log_cosh(x: torch.Tensor) -> torch.Tensor:
        return x + torch.nn.functional.softplus(-2. * x) - math.log(2.0)
    return torch.mean(_log_cosh(y_pred - y_true))
class LogCoshLoss(torch.nn.Module):
    def __init__(self):
        super().__init__()

    def forward(
        self, y_pred: torch.Tensor, y_true: torch.Tensor
    ) -> torch.Tensor:
        return log_cosh_loss(y_pred, y_true)


In [ ]:
import numpy as np
import random
import torch

def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)


set_random_seed(42)


In [ ]:
from sklearn.metrics import mean_absolute_error
def train_loop(dataloader, model, criterion, optimizer):
    num_batches = len(dataloader)

    train_loss = 0

    for imgs, labels in dataloader:
        # Compute prediction and loss
        pred = model(imgs.to(device)).squeeze(1)
        loss = criterion(pred, labels.to(device))

        # Optimization
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_loss += loss.item()

    train_loss /= num_batches
    print(f"Train loss: {train_loss:>8f}")

    return train_loss


def test_loop(dataloader, model, criterion, criterion_2):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    test_loss = 0
    test_loss_2 = 0

    with torch.no_grad():
        for imgs, labels in dataloader:
            # Compute prediction and loss
            pred = model(imgs.to(device)).squeeze(1)
            loss = criterion(pred, labels.to(device))
            #loss_2 = criterion_2(pred, labels.to(device))
            test_loss += loss.item()
            test_loss_2 += mean_absolute_error(pred.to('cpu').numpy(),labels.to('cpu').numpy())


    test_loss /= num_batches
    test_loss_2 /= num_batches
    print(f"Test loss: {test_loss:>8f}, test MRE: {test_loss_2} nm \n")

    return test_loss


In [ ]:
from tqdm import tqdm
optimizer = torch.optim.Adam(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss() # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_em_abs_rnn = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_em_abs_rnn["train"].append(train_loss)
    loss_history_em_abs_rnn["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//RNN_emission_abs.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models//RNN_emission_abs_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.04869658499956131
MAE : 23.859529495239258
RMSE : 34.07518768310547


# GRU_abs_em

In [ ]:
import torch.nn as nn
import torch

class BiDirectionalGRU(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, dropout):
        super(BiDirectionalGRU, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.dropout = nn.Dropout(dropout)

        self.gru = nn.GRU(input_size=input_size,
                         hidden_size=hidden_size,
                         num_layers=num_layers,
                         batch_first=True,
                          dropout = 0.2)

        self.fc = nn.Linear(hidden_size, 1)  # 2 for bidirectional

    def forward(self, x):
        # x shape: (batch_size, seq_len, input_size)
        out, _ = self.gru(x)
        out = self.dropout(out)

        # Take the final hidden state of the bidirectional GRU
        out = out[:, -1, :]  # (batch_size, hidden_size * 2)

        out = self.fc(out)
        return out

In [ ]:
import pickle
from tqdm import tqdm
model = BiDirectionalGRU(4322, 128, 2, 0.2)
model.to(device)


BiDirectionalGRU(
  (dropout): Dropout(p=0.2, inplace=False)
  (gru): GRU(4322, 128, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=128, out_features=1, bias=True)
)

In [ ]:
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)  # Weights update algorithm
criterion = LogCoshLoss()  # Loss function
criterion_2 = nn.L1Loss()
# for plotting
loss_history_gru_abs_em = {"train": [], "test": []}
num_epochs = 20000
best_loss = 100
for i in tqdm(range(num_epochs)):
    print(f"Epoch {i+1}")
    train_loss = train_loop(train_loader, model, criterion, optimizer)
    test_loss = test_loop(val_loader, model, criterion, criterion_2)

    loss_history_gru_abs_em["train"].append(train_loss)
    loss_history_gru_abs_em["test"].append(test_loss)
    if i//100:
        if test_loss<best_loss:
            torch.save(model, 'content/drive/MyDrive/MSU_AI_Photocatal/Models//GRU_abs_em.pt')
            torch.save(model.state_dict(), 'content/drive/MyDrive/MSU_AI_Photocatal/Models//GRU_abs_em_param.pth')
print("Done!")

In [ ]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error
y_pred = model(x_test.to(device)).squeeze(1).detach().to('cpu').numpy()
print(f'MRE : {mean_absolute_percentage_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'MAE : {mean_absolute_error(np.exp(y_test_solv), np.exp(y_pred))}')
print(f'RMSE : {mean_squared_error(np.exp(y_test_solv), np.exp(y_pred), squared=False)}')

MRE : 0.052901741117239
MAE : 26.233381271362305
RMSE : 37.18643569946289
